In [1]:
!pip install pgeocode
import numpy as np # library to handle data in a vectorized manner
!pip install geopy
!pip install folium
import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

from bs4 import BeautifulSoup


print('Libraries imported.')

/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/secretstorage/dhcrypto.py:16: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/secretstorage/util.py:25: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/secretstorage/dhcrypto.py:16: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/secretstorage/util.py:25: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/secretstorage/dhcrypto.py:16: Cryptograp

In [2]:
import pgeocode
nomi = pgeocode.Nominatim('SE')
nomi.query_postal_code("400 32")
#https://pgeocode.readthedocs.io/en/latest/overview.html#quickstart

postal_code                400 32
country_code                   SE
place_name               Göteborg
state_name        Västra Götaland
state_code                      O
county_name              Göteborg
county_code                  1480
community_name                NaN
community_code                NaN
latitude                  57.7072
longitude                 11.9668
accuracy                        4
Name: 0, dtype: object

In [3]:
#https://www.worldpostalcodes.org/l1/en/se/sweden/map/r2/map-of-postalcodes-in-goteborgs-stad
#https://goteborg.se/wps/wcm/connect/d30328ca-09c0-447d-8f96-954445b47efc/Omr%C3%A5deslista+2021.xlsx?MOD=AJPERES&CONVERT_TO=url&CACHEID=ROOTWORKSPACE-d30328ca-09c0-447d-8f96-954445b47efc-nEuesu6

In [4]:
html_wiki=requests.get('https://www.worldpostalcodes.org/l1/en/se/sweden/map/r2/map-of-postalcodes-in-goteborgs-stad').text
from bs4 import BeautifulSoup
soup = BeautifulSoup(html_wiki,'lxml')
print(soup.prettify())

<!DOCTYPE html>
<html lang="en">
 <head>
  <meta content="text/html; charset=utf-8" http-equiv="Content-Type"/>
  <meta content="IE=edge" http-equiv="X-UA-Compatible"/>
  <base href="//www.worldpostalcodes.org/"/>
  <title>
   Map of All Postal Codes in Göteborgs Stad July 2021
  </title>
  <meta name="twitter:site" value="@worldpostalcodes"/>
  <meta content="summary" name="twitter:card"/>
  <meta content="" name="twitter:title"/>
  <meta content="" name="twitter:description"/>
  <meta content="//www.worldpostalcodes.org/img/wpc.png" name="twitter:image"/>
  <meta content="" property="og:description"/>
  <meta content="article" property="og:type"/>
  <meta content="Worldpostalcodes.org" property="og:site_name"/>
  <meta content="//www.worldpostalcodes.org/img/wpc.png" property="og:image"/>
  <meta content="" property="og:title"/>
  <meta content="//www.worldpostalcodes.org/" property="og:url"/>
  <meta content="initial-scale=1.0, user-scalable=no" name="viewport"/>
  <script type="app

In [5]:
table_contents=[]
table=soup.find('table')

table2=table.findAll(class_= "mapzoom")

for link in table2:
    cell = {}
    #print(link.get('href'))
    #print(link.get('href').split('(')[1].split(')')[0].split(','))
    cell['PostalCode']=link.get('title').split(' ')[2].replace('-','')
    cell['latitude'] = link.get('href').split('(')[1].split(')')[0].split(',')[0]
    cell['longitude'] = link.get('href').split('(')[1].split(')')[0].split(',')[1]
    table_contents.append(cell)



In [6]:
goteborg_neigh=pd.DataFrame(table_contents)
goteborg_neigh.PostalCode.astype(str)
goteborg_neigh['PostalCode'] = goteborg_neigh['PostalCode'].astype( np.dtype(int))
goteborg_neigh.dtypes
goteborg_neigh.head()
goteborg_neigh.shape
print(goteborg_neigh)
#https://numpy.org/doc/stable/reference/arrays.dtypes.html
#https://stackoverflow.com/questions/39092067/pandas-dataframe-convert-column-type-to-string-or-categorical?rq=1
#https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.astype.html

     PostalCode     latitude    longitude
0         41101  57.70950699  11.98796272
1         41102  57.70892715  11.98471260
2         41103  57.70936203  11.97605896
3         41104  57.71588516  11.98299885
4         41105  57.70920181  11.96586609
5         41106  57.70690536  11.97275734
6         41107  57.70600128  11.97115803
7         41108  57.70523453  11.97196770
8         41109  57.70705414  11.96820831
9         41110  57.70352554  11.96933460
10        41111  57.70828247  11.98045063
11        41112  57.71131134  11.98712444
12        41113  57.70816040  11.96085072
13        41114  57.70595169  11.96469212
14        41115  57.70468903  11.96576118
15        41116  57.70372391  11.96525955
16        41117  57.70277405  11.96435738
17        41118  57.70435333  11.96044159
18        41119  57.70312881  11.95818901
19        41120  57.70166016  11.95948601
20        41121  57.70492554  11.95580101
21        41122  57.69629288  11.95855045
22        41123  57.69689560  11.9

In [7]:
link='https://goteborg.se/wps/wcm/connect/d30328ca-09c0-447d-8f96-954445b47efc/Omr%C3%A5deslista+2021.xlsx?MOD=AJPERES&CONVERT_TO=url&CACHEID=ROOTWORKSPACE-d30328ca-09c0-447d-8f96-954445b47efc-nEuesu6'
stadsdelar = pd.read_excel (link,sheets="alla områden")
stadsdelar['Basområde (NYKO)'] = stadsdelar['Basområde (NYKO)'].astype( np.dtype(int),errors='ignore')
stadsdelar.dtypes
#print(stadsdelar)
stadsdelar.head()
stadsdelar.shape

(1202, 5)

In [8]:
gothenburg_neigh=goteborg_neigh.merge(stadsdelar,how='left',left_on='PostalCode',right_on='Basområde (NYKO)')
gothenburg_neigh.head()
#print(goteborg_neigh)
#goteborg_neigh.shape

PostalCode     latitude    longitude Basområdet aktivt från 2021  \
0       41101  57.70950699  11.98796272                         Nej   
1       41102  57.70892715  11.98471260                         Nej   
2       41103  57.70936203  11.97605896                         Nej   
3       41104  57.71588516  11.98299885                         Nej   
4       41105  57.70920181  11.96586609                         Nej   

   Basområde (NYKO)   Primärområde Mellanområde 2021-    Stadsområde  
0           41101.0  413 Skälltorp           71 Backa  SO 4 Hisingen  
1           41102.0  413 Skälltorp           71 Backa  SO 4 Hisingen  
2           41103.0  413 Skälltorp           71 Backa  SO 4 Hisingen  
3           41104.0      412 Backa           71 Backa  SO 4 Hisingen  
4           41105.0      412 Backa           71 Backa  SO 4 Hisingen

In [10]:
#gothenburg_neigh=goteborg_neigh.drop(['Basområdet aktivt från 2021', 'Basområde (NYKO)'], axis=1)
#gothenburg_neigh.head()
#gothenburg_neigh.shape

In [11]:
address = 'Gothenburg Sweden'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Gothenburg Swenden are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Gothenburg Swenden are 57.7072326, 11.9670171.


In [13]:
# create map of New York using latitude and longitude values
map_gothenburg = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, borough, neighborhood in zip(gothenburg_neigh['latitude'], gothenburg_neigh['longitude'], gothenburg_neigh['Stadsområde'], gothenburg_neigh['Primärområde']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_gothenburg)  
    
map_gothenburg

In [14]:
CLIENT_ID = 'IU4KFW03GFBWDLW1C13ZACV2UAMKMSPG5ITQTLOISQ2WXRTJ' # your Foursquare ID
CLIENT_SECRET = 'GHYAGLAVOXRDGVZN3INEN5FU3EPTUWSZG4ZOSK1A5QKWLECE' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: IU4KFW03GFBWDLW1C13ZACV2UAMKMSPG5ITQTLOISQ2WXRTJ
CLIENT_SECRET:GHYAGLAVOXRDGVZN3INEN5FU3EPTUWSZG4ZOSK1A5QKWLECE


In [15]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [17]:
gothenburg_venues = getNearbyVenues(names=gothenburg_neigh['PostalCode'],
                                   latitudes=gothenburg_neigh['latitude'],
                                   longitudes=gothenburg_neigh['longitude']
                                  )

41101
41102
41103
41104
41105
41106
41107
41108
41109
41110
41111
41112
41113
41114
41115
41116
41117
41118
41119
41120
41121
41122
41123
41124
41125
41126
41127
41128
41129
41130
41131
41132
41133
41134
41135
41136
41137
41138
41139
41140
41143
41249
41250
41251
41252
41253
41254
41255
41256
41257
41258
41259
41260
41261
41262
41263
41264
41265
41266
41267
41268
41269
41270
41271
41272
41273
41274
41275
41276
41279
41280
41281
41282
41285
41301
41302
41303
41304
41305
41306
41307
41308
41309
41310
41311
41312
41313
41314
41315
41316
41317
41318
41319
41320
41321
41322
41323
41324
41325
41326
41327
41328
41346
41390
41451
41452
41453
41454
41455
41456
41457
41458
41459
41460
41461
41462
41463
41464
41465
41466
41467
41468
41469
41470
41471
41472
41473
41474
41475
41476
41477
41478
41479
41480
41481
41482
41483
41502
41505
41511
41512
41513
41514
41515
41516
41517
41522
41523
41524
41525
41526
41527
41528
41531
41532
41533
41534
41535
41536
41537
41538
41541
41542
41543
41544
41545
4154

In [27]:
print(gothenburg_venues.shape)
gothenburg_venues.head()

(5752, 7)


Neighborhood Neighborhood Latitude Neighborhood Longitude  \
0         41101           57.70950699            11.98796272   
1         41101           57.70950699            11.98796272   
2         41101           57.70950699            11.98796272   
3         41101           57.70950699            11.98796272   
4         41101           57.70950699            11.98796272   

                     Venue  Venue Latitude  Venue Longitude  \
0               Steamy Phở       57.709418        11.984937   
1               burgersson       57.711519        11.988393   
2  Ölstugan Tullen Lejonet       57.712370        11.990581   
3             I Love Pizza       57.711585        11.988510   
4          Glenn Sportsbar       57.710583        11.986655   

          Venue Category  
0  Vietnamese Restaurant  
1           Burger Joint  
2                    Pub  
3            Pizza Place  
4             Sports Bar

In [28]:
gothenburg_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                         
41101                            18                      18     18   
41102                            18                      18     18   
41103                            50                      50     50   
41104                             1                       1      1   
41105                            29                      29     29   
41106                            43                      43     43   
41107                            50                      50     50   
41108                            95                      95     95   
41109                            54                      54     54   
41110                           100                     100    100   
41111                            34                      34     34   
41112                            15                      15     15   
41113                            27                      27     27   
41114                            68                      68     68   
41115                            68                      68     68   
41116                           100                     100    100   
41117                           100                     100    100   
41118                           100                     100    100   
41119                           100                     100    100   
41120                            92                      92     92   
41121                            76                      76     76   
41122                            41                      41     41   
41123                            23                      23     23   
41124                            33                      33     33   
41125                            26                      26     26   
41126                            56                      56     56   
41127                            22                      22     22   
41128                            22                      22     22   
41129                            24                      24     24   
41130                            34                      34     34   
41131                            32                      32     32   
41132                            24                      24     24   
41133                            23                      23     23   
41134                            44                      44     44   
41135                            78                      78     78   
41136                            96                      96     96   
41137                            37                      37     37   
41138                            70                      70     70   
41139                            32                      32     32   
41140                            12                      12     12   
41143                            20                      20     20   
41249                             5                       5      5   
41250                             7                       7      7   
41251                            46                      46     46   
41252                            47                      47     47   
41253                            42                      42     42   
41254                            50                      50     50   
41255                            40                      40     40   
41256                            28                      28     28   
41257                            10                      10     10   
41258                            17                      17     17   
41259                            13                      13     13   
41260                            28                      28     28   
41261                            21                      21     21   
41262                             5                       5      5   
41263                   

In [30]:
print('There are {} uniques categories.'.format(len(gothenburg_venues['Venue Category'].unique())))

There are 241 uniques categories.


In [32]:
# one hot encoding
gothenburg_onehot = pd.get_dummies(gothenburg_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
gothenburg_onehot['Neighborhood'] = gothenburg_venues['Neighborhood'] 



# move neighborhood column to the first column
fixed_columns = [gothenburg_onehot.columns[-1]] + list(gothenburg_onehot.columns[:-1])
gothenburg_onehot = gothenburg_onehot[fixed_columns]

gothenburg_onehot.head()

Neighborhood  Adult Boutique  American Restaurant  Arcade  Art Gallery  \
0         41101               0                    0       0            0   
1         41101               0                    0       0            0   
2         41101               0                    0       0            0   
3         41101               0                    0       0            0   
4         41101               0                    0       0            0   

   Art Museum  Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0           0                    0                     0                 0   
1           0                    0                     0                 0   
2           0                    0                     0                 0   
3           0                    0                     0                 0   
4           0                    0                     0                 0   

   Athletics & Sports  Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  \
0                   0            0              0                0          0   
1                   0            0              0                0          0   
2                   0            0              0                0          0   
3                   0            0              0                0          0   
4                   0            0              0                0          0   

   Baby Store  Badminton Court  Bagel Shop  Bakery  Bar  Baseball Field  \
0           0                0           0       0    0               0   
1           0                0           0       0    0               0   
2           0                0           0       0    0               0   
3           0                0           0       0    0               0   
4           0                0           0       0    0               0   

   Basketball Court  Bathing Area  Beach  Beach Bar  Bed & Breakfast  \
0                 0             0      0          0                0   
1                 0             0      0          0                0   
2                 0             0      0          0                0   
3                 0             0      0          0                0   
4                 0             0      0          0                0   

   Beer Bar  Beer Garden  Beer Store  Bistro  Boat or Ferry  Bookstore  \
0         0            0           0       0              0          0   
1         0            0           0       0              0          0   
2         0            0           0       0              0          0   
3         0            0           0       0              0          0   
4         0            0           0       0              0          0   

   Botanical Garden  Bowling Alley  Brazilian Restaurant  Breakfast Spot  \
0                 0              0                     0               0   
1                 0              0                     0               0   
2                 0              0                     0               0   
3                 0              0                     0               0   
4                 0              0                     0               0   

   Brewery  Buffet  Burger Joint  Burrito Place  Bus Station  Bus Stop  \
0        0       0             0              0            0         0   
1        0       0             1              0            0         0   
2        0       0             0              0            0         0   
3        0       0             0              0            0         0   
4        0       0             0              0            0         0   

   Business Service  Café  Cajun / Creole Restaurant  Campground  Candy Store  \
0                 0     0                          0           0            0   
1                 0     0                          0           0            0   
2                 0     0                          0           0            0   
3                 0     0    

In [34]:
gothenburg_onehot.shape
gothenburg_grouped = gothenburg_onehot.groupby('Neighborhood').mean().reset_index()
gothenburg_grouped 

Neighborhood  Adult Boutique  American Restaurant    Arcade  Art Gallery  \
0           41101             0.0             0.000000  0.000000     0.000000   
1           41102             0.0             0.000000  0.000000     0.000000   
2           41103             0.0             0.020000  0.000000     0.000000   
3           41104             0.0             0.000000  0.000000     0.000000   
4           41105             0.0             0.034483  0.000000     0.000000   
5           41106             0.0             0.023256  0.000000     0.000000   
6           41107             0.0             0.020000  0.000000     0.000000   
7           41108             0.0             0.021053  0.000000     0.010526   
8           41109             0.0             0.018519  0.000000     0.000000   
9           41110             0.0             0.010000  0.000000     0.010000   
10          41111             0.0             0.029412  0.000000     0.000000   
11          41112             0.0             0.000000  0.000000     0.000000   
12          41113             0.0             0.000000  0.000000     0.000000   
13          41114             0.0             0.000000  0.000000     0.000000   
14          41115             0.0             0.000000  0.014706     0.000000   
15          41116             0.0             0.000000  0.000000     0.010000   
16          41117             0.0             0.000000  0.000000     0.010000   
17          41118             0.0             0.000000  0.010000     0.010000   
18          41119             0.0             0.000000  0.010000     0.010000   
19          41120             0.0             0.000000  0.010870     0.010870   
20          41121             0.0             0.000000  0.013158     0.013158   
21          41122             0.0             0.024390  0.000000     0.000000   
22          41123             0.0             0.000000  0.000000     0.000000   
23          41124             0.0             0.000000  0.000000     0.000000   
24          41125             0.0             0.000000  0.000000     0.000000   
25          41126             0.0             0.017857  0.000000     0.000000   
26          41127             0.0             0.000000  0.000000     0.000000   
27          41128             0.0             0.000000  0.000000     0.000000   
28          41129             0.0             0.000000  0.000000     0.000000   
29          41130             0.0             0.000000  0.000000     0.000000   
30          41131             0.0             0.000000  0.000000     0.000000   
31          41132             0.0             0.000000  0.000000     0.000000   
32          41133             0.0             0.000000  0.000000     0.000000   
33          41134             0.0             0.000000  0.000000     0.000000   
34          41135             0.0             0.012821  0.000000     0.000000   
35          41136             0.0             0.010417  0.010417     0.010417   
36          41137             0.0             0.000000  0.000000     0.000000   
37          41138             0.0             0.028571  0.000000     0.000000   
38          41139             0.0             0.031250  0.000000     0.000000   
39          41140             0.0             0.000000  0.000000     0.000000   
40          41143             0.0             0.050000  0.000000     0.000000   
41          41249             0.0             0.000000  0.000000     0.000000   
42          41250             0.0             0.000000  0.000000     0.000000   
43          41251             0.0             0.000000  0.000000     0.000000   
44          41252             0.0             0.000000  0.000000     0.000000   
45          41253             0.0             0.000000  0.000000     0.000000   
46          41254             0.0             0.000000  0.020000     0.000000   
47          41255             0.0             0.000000  0.000000     0.000000   
48          41256             0.0   

In [36]:
num_top_venues = 5

for hood in gothenburg_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = gothenburg_grouped[gothenburg_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

TypeError: can only concatenate str (not "int") to str

In [37]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [40]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = gothenburg_grouped['Neighborhood']

for ind in np.arange(gothenburg_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(gothenburg_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0         41101                   Pub                 Hotel   
1         41102                 Hotel                   Pub   
2         41103                 Hotel           Coffee Shop   
3         41104         Historic Site         Women's Store   
4         41105                 Hotel                   Pub   

  3rd Most Common Venue 4th Most Common Venue    5th Most Common Venue  \
0    Light Rail Station          Burger Joint            Burrito Place   
1                   Bar         Bowling Alley             Burger Joint   
2     Convenience Store      Sushi Restaurant           Clothing Store   
3    Falafel Restaurant     French Restaurant              Frame Store   
4                  Café           Coffee Shop  Scandinavian Restaurant   

  6th Most Common Venue    7th Most Common Venue 8th Most Common Venue  \
0            Sports Bar                  Stadium      Sushi Restaurant   
1         Burrito Place               Sports Bar               Stadium   
2             Hotel Bar  Scandinavian Restaurant     Electronics Store   
3            Food Truck               Food Stand            Food Court   
4     Electronics Store              Opera House                Bistro   

  9th Most Common Venue    10th Most Common Venue  
0      Tapas Restaurant                Bagel Shop  
1  Fast Food Restaurant          Sushi Restaurant  
2                  Park       Sporting Goods Shop  
3     Food & Drink Shop                      Food  
4    Seafood Restaurant  Mediterranean Restaurant

In [42]:
# set number of clusters
kclusters = 6

gothenburg_grouped_clustering = gothenburg_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(gothenburg_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 



array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [47]:
gothenburg_merged.head()

PostalCode     latitude    longitude Basområdet aktivt från 2021  \
0       41101  57.70950699  11.98796272                         Nej   
1       41102  57.70892715  11.98471260                         Nej   
2       41103  57.70936203  11.97605896                         Nej   
3       41104  57.71588516  11.98299885                         Nej   
4       41105  57.70920181  11.96586609                         Nej   

   Basområde (NYKO)   Primärområde Mellanområde 2021-    Stadsområde  
0           41101.0  413 Skälltorp           71 Backa  SO 4 Hisingen  
1           41102.0  413 Skälltorp           71 Backa  SO 4 Hisingen  
2           41103.0  413 Skälltorp           71 Backa  SO 4 Hisingen  
3           41104.0      412 Backa           71 Backa  SO 4 Hisingen  
4           41105.0      412 Backa           71 Backa  SO 4 Hisingen

In [49]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

gothenburg_merged = gothenburg_neigh

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
gothenburg_merged = gothenburg_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='PostalCode')

gothenburg_merged.head() # check the last columns!

PostalCode     latitude    longitude Basområdet aktivt från 2021  \
0       41101  57.70950699  11.98796272                         Nej   
1       41102  57.70892715  11.98471260                         Nej   
2       41103  57.70936203  11.97605896                         Nej   
3       41104  57.71588516  11.98299885                         Nej   
4       41105  57.70920181  11.96586609                         Nej   

   Basområde (NYKO)   Primärområde Mellanområde 2021-    Stadsområde  \
0           41101.0  413 Skälltorp           71 Backa  SO 4 Hisingen   
1           41102.0  413 Skälltorp           71 Backa  SO 4 Hisingen   
2           41103.0  413 Skälltorp           71 Backa  SO 4 Hisingen   
3           41104.0      412 Backa           71 Backa  SO 4 Hisingen   
4           41105.0      412 Backa           71 Backa  SO 4 Hisingen   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0             0.0                   Pub                 Hotel   
1             0.0                 Hotel                   Pub   
2             0.0                 Hotel           Coffee Shop   
3             0.0         Historic Site         Women's Store   
4             0.0                 Hotel                   Pub   

  3rd Most Common Venue 4th Most Common Venue    5th Most Common Venue  \
0    Light Rail Station          Burger Joint            Burrito Place   
1                   Bar         Bowling Alley             Burger Joint   
2     Convenience Store      Sushi Restaurant           Clothing Store   
3    Falafel Restaurant     French Restaurant              Frame Store   
4                  Café           Coffee Shop  Scandinavian Restaurant   

  6th Most Common Venue    7th Most Common Venue 8th Most Common Venue  \
0            Sports Bar                  Stadium      Sushi Restaurant   
1         Burrito Place               Sports Bar               Stadium   
2             Hotel Bar  Scandinavian Restaurant     Electronics Store   
3            Food Truck               Food Stand            Food Court   
4     Electronics Store              Opera House                Bistro   

  9th Most Common Venue    10th Most Common Venue  
0      Tapas Restaurant                Bagel Shop  
1  Fast Food Restaurant          Sushi Restaurant  
2                  Park       Sporting Goods Shop  
3     Food & Drink Shop                      Food  
4    Seafood Restaurant  Mediterranean Restaurant

In [52]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)
import math

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]
print(rainbow)


# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(gothenburg_merged['latitude'], gothenburg_merged['longitude'], gothenburg_merged['PostalCode'], gothenburg_merged['Cluster Labels']):
    
    if (math.isnan(cluster)):
       cluster=0
    
    
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

['#8000ff', '#1996f3', '#4df3ce', '#b2f396', '#ff964f', '#ff0000']


In [54]:
gothenburg_merged.loc[gothenburg_merged['Cluster Labels'] == 0, gothenburg_merged.columns[[0] + list(range(5, gothenburg_merged.shape[1]))]]

PostalCode        Primärområde         Mellanområde 2021-    Stadsområde  \
0         41101       413 Skälltorp                   71 Backa  SO 4 Hisingen   
1         41102       413 Skälltorp                   71 Backa  SO 4 Hisingen   
2         41103       413 Skälltorp                   71 Backa  SO 4 Hisingen   
3         41104           412 Backa                   71 Backa  SO 4 Hisingen   
4         41105           412 Backa                   71 Backa  SO 4 Hisingen   
5         41106           412 Backa                   71 Backa  SO 4 Hisingen   
6         41107           412 Backa                   71 Backa  SO 4 Hisingen   
7         41108           412 Backa                   71 Backa  SO 4 Hisingen   
8         41109       413 Skälltorp                   71 Backa  SO 4 Hisingen   
9         41110       413 Skälltorp                   71 Backa  SO 4 Hisingen   
10        41111       413 Skälltorp                   71 Backa  SO 4 Hisingen   
11        41112       413 Skälltorp                   71 Backa  SO 4 Hisingen   
12        41113       413 Skälltorp                   71 Backa  SO 4 Hisingen   
13        41114       413 Skälltorp                   71 Backa  SO 4 Hisingen   
14        41115       413 Skälltorp                   71 Backa  SO 4 Hisingen   
15        41116           412 Backa                   71 Backa  SO 4 Hisingen   
16        41117                 NaN                        NaN            NaN   
17        41118                 NaN                        NaN            NaN   
18        41119                 NaN                        NaN            NaN   
19        41120                 NaN                        NaN            NaN   
20        41121                 NaN                        NaN            NaN   
21        41122                 NaN                        NaN            NaN   
22        41123                 NaN                        NaN            NaN   
23        41124                 NaN                        NaN            NaN   
24        41125                 NaN                        NaN            NaN   
25        41126                 NaN                        NaN            NaN   
26        41127                 NaN                        NaN            NaN   
27        41128                 NaN                        NaN            NaN   
28        41129                 NaN                        NaN            NaN   
29        41130                 NaN                        NaN            NaN   
30        41131                 NaN                        NaN            NaN   
31        41132                 NaN                        NaN            NaN   
32        41133                 NaN                        NaN            NaN   
33        41134                 NaN                        NaN            NaN   
34        41135                 NaN                        NaN            NaN   
35        41136                 NaN                        NaN            NaN   
36        41137                 NaN                        NaN            NaN   
37        41138                 NaN                        NaN            NaN   
38        41139                 NaN                        NaN            NaN   
39        41140                 NaN                        NaN            NaN   
40        41143                 NaN                        NaN            NaN   
42        41250                 NaN                        NaN            NaN   
43        41251           412 Backa                   71 Backa  SO 4 Hisingen   
44        41252           412 Backa                   71 Backa  SO 4 Hisingen   
45        41253           412 Backa                   71 Backa  SO 4 Hisingen   
46        41254                 NaN                        NaN            NaN   
47        41255                 NaN                        NaN            NaN   
48        41256                 NaN                        NaN            NaN   
49        41257                 NaN 

In [56]:
gothenburg_merged.loc[gothenburg_merged['Cluster Labels'] == 1, gothenburg_merged.columns[[0] + list(range(5, gothenburg_merged.shape[1]))]]

PostalCode        Primärområde         Mellanområde 2021-    Stadsområde  \
41        41249                 NaN                        NaN            NaN   
64        41272                 NaN                        NaN            NaN   
65        41273                 NaN                        NaN            NaN   
93        41320                 NaN                        NaN            NaN   
121       41468                 NaN                        NaN            NaN   
138       41505  415 Rambergsstaden  73 Kyrkbyn-Rambergsstaden  SO 4 Hisingen   
153       41531                 NaN                        NaN            NaN   
155       41533                 NaN                        NaN            NaN   
165       41545                 NaN                        NaN            NaN   
167       41547                 NaN                        NaN            NaN   
168       41548                 NaN                        NaN            NaN   
171       41553  415 Rambergsstaden  73 Kyrkbyn-Rambergsstaden  SO 4 Hisingen   
175       41557                 NaN                        NaN            NaN   
177       41562                 NaN                        NaN            NaN   
180       41565                 NaN                        NaN            NaN   
182       41567                 NaN                        NaN            NaN   
193       41652       416 Eriksberg       74 Norra Älvstranden  SO 4 Hisingen   
217       41676                 NaN                        NaN            NaN   
269       41831                 NaN                        NaN            NaN   
271       41833                 NaN                        NaN            NaN   
273       41835                 NaN                        NaN            NaN   
274       41836                 NaN                        NaN            NaN   
275       41837                 NaN                        NaN            NaN   
276       41838                 NaN                        NaN            NaN   
277       41839                 NaN                        NaN            NaN   
280       41842                 NaN                        NaN            NaN   
281       41843                 NaN                        NaN            NaN   
282       41870                 NaN                        NaN            NaN   
284       41872                 NaN                        NaN            NaN   
381       42435                 NaN                        NaN            NaN   
382       42436                 NaN                        NaN            NaN   
383       42437                 NaN                        NaN            NaN   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
41              1.0    Light Rail Station  Gym / Fitness Center   
64              1.0    Light Rail Station           Pizza Place   
65              1.0    Light Rail Station                   Spa   
93              1.0    Light Rail Station                Garden   
121             1.0    Light Rail Station           Pizza Place   
138             1.0    Light Rail Station           Flea Market   
153             1.0    Light Rail Station             BBQ Joint   
155             1.0    Light Rail Station             BBQ Joint   
165             1.0    Light Rail Station           Pizza Place   
167             1.0    Light Rail Station           Pizza Place   
168             1.0    Light Rail Station           Supermarket   
171             1.0    Light Rail Station           Pizza Place   
175             1.0    Light Rail Station           Pizza Place   
177             1.0         Moving Target    Light Rail Station   
180             1.0    Light Rail Station                 Plaza   
182             1.0    Light Rail Station                Casino   
193             1.0    Light Rail Station                Bakery   
217             1.0    Light Rail Station         Women's Store   
269             1.0    Light Rail Station         Grocery 

In [58]:
gothenburg_merged.loc[gothenburg_merged['Cluster Labels'] == 2, gothenburg_merged.columns[[0] + list(range(5, gothenburg_merged.shape[1]))]]

PostalCode        Primärområde         Mellanområde 2021-    Stadsområde  \
54        41262                 NaN                        NaN            NaN   
59        41267                 NaN                        NaN            NaN   
61        41269                 NaN                        NaN            NaN   
62        41270                 NaN                        NaN            NaN   
69        41279                 NaN                        NaN            NaN   
95        41322                 NaN                        NaN            NaN   
98        41325                 NaN                        NaN            NaN   
99        41326                 NaN                        NaN            NaN   
109       41456                 NaN                        NaN            NaN   
110       41457                 NaN                        NaN            NaN   
117       41464                 NaN                        NaN            NaN   
118       41465                 NaN                        NaN            NaN   
119       41466                 NaN                        NaN            NaN   
120       41467                 NaN                        NaN            NaN   
126       41473                 NaN                        NaN            NaN   
130       41477                 NaN                        NaN            NaN   
131       41478                 NaN                        NaN            NaN   
132       41479                 NaN                        NaN            NaN   
133       41480                 NaN                        NaN            NaN   
134       41481                 NaN                        NaN            NaN   
135       41482                 NaN                        NaN            NaN   
147       41523                 NaN                        NaN            NaN   
148       41524                 NaN                        NaN            NaN   
150       41526                 NaN                        NaN            NaN   
156       41534                 NaN                        NaN            NaN   
160       41538                 NaN                        NaN            NaN   
161       41541                 NaN                        NaN            NaN   
162       41542                 NaN                        NaN            NaN   
163       41543                 NaN                        NaN            NaN   
170       41552  415 Rambergsstaden  73 Kyrkbyn-Rambergsstaden  SO 4 Hisingen   
172       41554  415 Rambergsstaden  73 Kyrkbyn-Rambergsstaden  SO 4 Hisingen   
173       41555                 NaN                        NaN            NaN   
174       41556                 NaN                        NaN            NaN   
178       41563                 NaN                        NaN            NaN   
179       41564                 NaN                        NaN            NaN   
192       41651       416 Eriksberg       74 Norra Älvstranden  SO 4 Hisingen   
197       41656                 NaN                        NaN            NaN   
211       41670                 NaN                        NaN            NaN   
213       41672                 NaN                        NaN            NaN   
227       41705      417 Lindholmen       74 Norra Älvstranden  SO 4 Hisingen   
237       41719      417 Lindholmen       74 Norra Älvstranden  SO 4 Hisingen   
239       41721      417 Lindholmen       74 Norra Älvstranden  SO 4 Hisingen   
245       41728                 NaN                        NaN            NaN   
248       41743                 NaN                        NaN            NaN   
261       41761                 NaN                        NaN            NaN   
278       41840                 NaN                        NaN            NaN   
279       41841                 NaN                        NaN            NaN   
283       41871                 NaN                        NaN            NaN   
286       41874                 NaN 

In [59]:
gothenburg_merged.loc[gothenburg_merged['Cluster Labels'] == 3, gothenburg_merged.columns[[0] + list(range(5, gothenburg_merged.shape[1]))]]

PostalCode    Primärområde    Mellanområde 2021-    Stadsområde  \
176       41561             NaN                   NaN            NaN   
218       41677             NaN                   NaN            NaN   
219       41678             NaN                   NaN            NaN   
244       41727  417 Lindholmen  74 Norra Älvstranden  SO 4 Hisingen   
334       42245             NaN                   NaN            NaN   
344       42255             NaN                   NaN            NaN   
353       42337             NaN                   NaN            NaN   
361       42347             NaN                   NaN            NaN   
362       42349             NaN                   NaN            NaN   
380       42434             NaN                   NaN            NaN   
385       42439             NaN                   NaN            NaN   
388       42442             NaN                   NaN            NaN   
389       42443             NaN                   NaN            NaN   
390       42444             NaN                   NaN            NaN   
391       42445             NaN                   NaN            NaN   
392       42446             NaN                   NaN            NaN   
413       42530             NaN                   NaN            NaN   
470       43644             NaN                   NaN            NaN   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
176             3.0                  Lake          Soccer Field   
218             3.0              Bus Stop              Pharmacy   
219             3.0              Bus Stop           Pizza Place   
244             3.0          Soccer Field              Bus Stop   
334             3.0              Bus Stop         Grocery Store   
344             3.0                  Farm              Bus Stop   
353             3.0   Japanese Restaurant              Bus Stop   
361             3.0              Bus Stop              Ski Area   
362             3.0          Concert Hall              Bus Stop   
380             3.0              Bus Stop                Market   
385             3.0              Bus Stop      Business Service   
388             3.0              Bus Stop         Women's Store   
389             3.0              Bus Stop         Women's Store   
390             3.0                  Lake              Bus Stop   
391             3.0              Bus Stop                  Lake   
392             3.0              Bus Stop                  Lake   
413             3.0              Bus Stop           Pizza Place   
470             3.0              Bus Stop           Golf Course   

    3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
176              Bus Stop           Women's Store                  Farm   
218           Pizza Place           Women's Store           Frame Store   
219         Women's Store                    Farm     French Restaurant   
244                  Lake                   Plaza         Women's Store   
334           Pizza Place           Women's Store                  Farm   
344  Fast Food Restaurant            Dance Studio    Frozen Yogurt Shop   
353         Women's Store                    Farm    Frozen Yogurt Shop   
361         Women's Store  Furniture / Home Store     French Restaurant   
362         Women's Store                    Farm     French Restaurant   
380         Women's Store                    Farm    Frozen Yogurt Shop   
385         Women's Store  Furniture / Home Store     French Restaurant   
388          Dance Studio      Frozen Yogurt Shop     French Restaurant   
389          Dance Studio      Frozen Yogurt Shop     French Restaurant   
390         Women's Store                    Farm    Frozen Yogurt Shop   
391                 Beach           Women's Store  Fast Food Restaurant   
392                 Beach           Women's Store  Fast Food Restaurant   
413         Women's Store                    Farm     French Restaurant   
470   Sporti

In [61]:
gothenburg_merged.loc[gothenburg_merged['Cluster Labels'] == 4, gothenburg_merged.columns[[0] + list(range(5, gothenburg_merged.shape[1]))]]

PostalCode Primärområde Mellanområde 2021- Stadsområde  Cluster Labels  \
320       42162          NaN                NaN         NaN             4.0   
323       42166          NaN                NaN         NaN             4.0   
355       42339          NaN                NaN         NaN             4.0   
393       42447          NaN                NaN         NaN             4.0   
478       43656          NaN                NaN         NaN             4.0   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
320                 Beach         Women's Store                Garden   
323                 Beach         Women's Store                Garden   
355   Housing Development                 Beach                Garden   
393                  Lake                 Beach         Women's Store   
478                 Beach         Women's Store                Garden   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
320    Frozen Yogurt Shop     French Restaurant           Frame Store   
323    Frozen Yogurt Shop     French Restaurant           Frame Store   
355    Frozen Yogurt Shop     French Restaurant           Frame Store   
393                  Farm    Frozen Yogurt Shop     French Restaurant   
478    Frozen Yogurt Shop     French Restaurant           Frame Store   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
320            Food Truck            Food Stand            Food Court   
323            Food Truck            Food Stand            Food Court   
355            Food Truck            Food Stand            Food Court   
393           Frame Store            Food Truck            Food Stand   
478            Food Truck            Food Stand            Food Court   

    10th Most Common Venue  
320      Food & Drink Shop  
323      Food & Drink Shop  
355      Food & Drink Shop  
393             Food Court  
478      Food & Drink Shop

In [60]:
gothenburg_merged.loc[gothenburg_merged['Cluster Labels'] == 5, gothenburg_merged.columns[[0] + list(range(5, gothenburg_merged.shape[1]))]]

PostalCode Primärområde Mellanområde 2021- Stadsområde  Cluster Labels  \
252       41747          NaN                NaN         NaN             5.0   
336       42247          NaN                NaN         NaN             5.0   
368       42355          NaN                NaN         NaN             5.0   
374       42371          NaN                NaN         NaN             5.0   
376       42373          NaN                NaN         NaN             5.0   
405       42467          NaN                NaN         NaN             5.0   
406       42468          NaN                NaN         NaN             5.0   
408       42470          NaN                NaN         NaN             5.0   
433       42656          NaN                NaN         NaN             5.0   

    1st Most Common Venue       2nd Most Common Venue 3rd Most Common Venue  \
252           Sports Club                  Playground         Women's Store   
336            Playground                       Trail         Women's Store   
368            Playground               Women's Store                  Farm   
374            Playground               Women's Store                  Farm   
376            Playground               Women's Store                  Farm   
405           Flea Market                  Playground         Women's Store   
406            Playground               Women's Store                  Farm   
408            Playground  Construction & Landscaping                  Lake   
433            Playground               Women's Store                  Farm   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
252    Falafel Restaurant     French Restaurant           Frame Store   
336    Falafel Restaurant     French Restaurant           Frame Store   
368    Frozen Yogurt Shop     French Restaurant           Frame Store   
374    Frozen Yogurt Shop     French Restaurant           Frame Store   
376    Frozen Yogurt Shop     French Restaurant           Frame Store   
405                  Farm    Frozen Yogurt Shop     French Restaurant   
406    Frozen Yogurt Shop     French Restaurant           Frame Store   
408    Falafel Restaurant     French Restaurant           Frame Store   
433    Frozen Yogurt Shop     French Restaurant           Frame Store   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
252            Food Truck            Food Stand            Food Court   
336            Food Truck            Food Stand            Food Court   
368            Food Truck            Food Stand            Food Court   
374            Food Truck            Food Stand            Food Court   
376            Food Truck            Food Stand            Food Court   
405           Frame Store            Food Truck            Food Stand   
406            Food Truck            Food Stand            Food Court   
408            Food Truck            Food Stand            Food Court   
433            Food Truck            Food Stand            Food Court   

    10th Most Common Venue  
252      Food & Drink Shop  
336      Food & Drink Shop  
368      Food & Drink Shop  
374      Food & Drink Shop  
376      Food & Drink Shop  
405             Food Court  
406      Food & Drink Shop  
408      Food & Drink Shop  
433      Food & Drink Shop